### Multiprocessing

In [ ]:
# !!! will not run in the notebook !!!

# import multiprocessing

# def printer(num):
#     print(num)
    
# with multiprocessing.Pool() as pool:
#     pool.map(printer, range(5))

In [29]:
%%writefile test-multiprocessing.py
import multiprocessing

def square(num):
    return num * num
    
if __name__ == '__main__':
    __spec__ = None    
    with multiprocessing.Pool(5) as pool:
        result = pool.map(square, range(5))
        print(result)

Overwriting test-multiprocessing.py


In [30]:
%run test-multiprocessing.py

[0, 1, 4, 9, 16]


In [37]:
import concurrent.futures
import multiprocessing as mp
import time

def dummy(num):
    time.sleep(0.5)
    return num ** 2

start_time = time.time()
with concurrent.futures.ProcessPoolExecutor(max_workers=5, mp_context=mp.get_context('fork')) as executor:
    results = executor.map(dummy, range(10))
print("Total Time:", time.time() - start_time)

Total Time: 1.036273717880249


In [38]:
for r in results:
    print(r)

0
1
4
9
16
25
36
49
64
81


### Comparing single-thread, multi-thread, and asyncio

[Example by J. Anderson](https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program)

In [39]:
# https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program

import requests
import time

def download_site(url, session):
    with session.get(url) as response:
        # print(f"Read {len(response.content)} from {url}")
        pass

def download_all_sites(sites):
    with requests.Session() as session:
        for url in sites:
            download_site(url, session)

if __name__ == "__main__":
    sites = [
        "https://www.jython.org",
        "http://olympus.realpython.org/dice",
    ] * 80
    start_time = time.time()
    download_all_sites(sites)
    duration = time.time() - start_time
    print(f"Downloaded {len(sites)} in {duration} seconds")

Downloaded 160 in 4.459496974945068 seconds


In [40]:
# https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program

import concurrent.futures
import requests
import threading
import time

thread_local = threading.local()

def get_session():
    if not hasattr(thread_local, "session"):
        thread_local.session = requests.Session()
    return thread_local.session

def download_site(url):
    session = get_session()
    with session.get(url) as response:
        # print(f"Read {len(response.content)} from {url}")
        pass

def download_all_sites(sites):
    with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
        executor.map(download_site, sites)

if __name__ == "__main__":
    sites = [
        "https://www.jython.org",
        "http://olympus.realpython.org/dice",
    ] * 80
    start_time = time.time()
    download_all_sites(sites)
    duration = time.time() - start_time
    print(f"Downloaded {len(sites)} in {duration} seconds")

Downloaded 160 in 0.9209921360015869 seconds


In [41]:
# !pip install nest_asyncio
import nest_asyncio

nest_asyncio.apply()

In [44]:
# https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program

import asyncio
import time
import aiohttp

async def download_site(session, url):
    async with session.get(url) as response:
        # print("Read {0} from {1}".format(response.content_length, url))
        pass

async def download_all_sites(sites):
    async with aiohttp.ClientSession() as session:
        tasks = []
        for url in sites:
            task = asyncio.ensure_future(download_site(session, url))
            tasks.append(task)
        await asyncio.gather(*tasks, return_exceptions=True)

if __name__ == "__main__":
    sites = [
        "https://www.jython.org",
        "http://olympus.realpython.org/dice",
    ] * 80
    start_time = time.time()
    asyncio.get_event_loop().run_until_complete(download_all_sites(sites))
    duration = time.time() - start_time
    print(f"Downloaded {len(sites)} sites in {duration} seconds")

Downloaded 160 sites in 0.2759230136871338 seconds


In [ ]:
# this is not a function call, creates a coroutine object!
download_site("foo", "bar")

### Match Statement Alternatives

In [45]:
vals = [45, 1, 2, 3]
for val in vals:
    if val == 1:
        print('1st')
    elif val == 2:
        print('2nd')
    else:
        print('???')

???
1st
2nd
???


In [46]:
vals = [45, 1, 2, 3]
for val in vals:
    ops = {
        1: lambda: print('1st'),
        2: lambda: print('2nd')
    }
    ops.get(val, lambda: print('???'))()

???
1st
2nd
???


### The Match Statement

In [47]:
vals = [45, 1, 2, 3]
for val in vals:
    match val:
        case 1:
            print(val, '1st')
        case 2:
            print(val, '2nd')
        case _:
            print(val, '???')

45 ???
1 1st
2 2nd
3 ???


In [48]:
argvs = [
    ['git', 'commit'],
    ['git', 'add'],
    ['git', 'add', 'b.txt'],
    ['git', 'add', 'c.txt', 'd.txt']
]

[['git', 'commit'],
 ['git', 'add'],
 ['git', 'add', 'b.txt'],
 ['git', 'add', 'c.txt', 'd.txt']]

In [49]:
for argv in argvs:
    print(argv)
    match argv:
        case [_, 'commit']:
            print("Committing")
        case [_, 'add', fname]:
            print("Adding file", fname)

['git', 'commit']
Committing
['git', 'add']
['git', 'add', 'b.txt']
Adding file b.txt
['git', 'add', 'c.txt', 'd.txt']


In [50]:
for argv in argvs:
    print(argv)
    match argv:
        case [_, 'commit']:
            print("Committing")
        case [_, 'add', fname, _]:
            print("Adding file", fname)

['git', 'commit']
Committing
['git', 'add']
['git', 'add', 'b.txt']
['git', 'add', 'c.txt', 'd.txt']
Adding file c.txt


In [51]:
a, *rest = [1,2,3,4]

In [52]:
rest

[2, 3, 4]

In [53]:
for argv in argvs:
    print(argv)
    match argv:
        case [_, 'commit']:
            print("Committing")
        case [_, 'add', *fnames]:
            print("Adding files", fnames)

['git', 'commit']
Committing
['git', 'add']
Adding files []
['git', 'add', 'b.txt']
Adding files ['b.txt']
['git', 'add', 'c.txt', 'd.txt']
Adding files ['c.txt', 'd.txt']


### Or and As Pattern

In [54]:
commands = [
    "go north",
    "pick candlestick up",
    "pick up wrench",
    "north"
]
for command in commands:
    match command.split():
        # Other cases
        case ["north"] | ["go", "north"]:
            print("Going north")
        case ["pick", "up", obj] | ["pick", obj, "up"]:
            print("Picking up", obj)

Going north
Picking up candlestick
Picking up wrench
Going north


In [55]:
commands = [
    "go north",
    "go east",
    "go up",
    "go south"
]
for command in commands:
    match command.split():
        # Other cases
        case ["go", ("north" | "east" | "west" | "south")]:
            print("Going somewhere...")

Going somewhere...
Going somewhere...
Going somewhere...


In [56]:
commands = [
    "go north",
    "go east",
    "go up",
    "go south"
]
for command in commands:
    match command.split():
        # Other cases
        case ["go", ("north" | "east" | "west" | "south") as d]:
            print("Going", d)

Going north
Going east
Going south


In [57]:
commands = [
    "go north",
    "go east",
    "go up",
    "go south"
]
for command in commands:
    match command.split():
        # Other cases
        case ["go", ("north" | "east" | "west" | "south") as d]:
            print("Going", d)
        case ["go", _ as d]:
            print("Cannot go", d)

Going north
Going east
Cannot go up
Going south


In [58]:
commands = [
    "go north",
    "go east",
    "go up",
    "go south"
]
for command in commands:
    match command.split():
        # Other cases
        case ["go", ("north" | "east" | "west" | "south") as d]:
            pass
        case ["go", _ as d]:
            print("Cannot go", d)

Cannot go up


### Guards

In [59]:
commands = [
    "go north",
    "go east",
    "go up",
    "go south"
]
for command in commands:
    match command.split():
        # Other cases
        case ["go", _ as d] if d not in {'north','south','east','west'}:
            print("Cannot go", d)

Cannot go up


In [60]:
class Room:
    def __init__(self, exits=[]):
        self.exits = list(exits)

    def neighbor(self, dir):
        print("GOING", dir)

current_room = Room(["east", "north"])

commands = [
    "go north",
    "go east",
    "go up",
    "go south"
]

for command in commands:      
    match command.split():
        case ["go", dir] if dir in current_room.exits:
            current_room.neighbor(dir)
        case ["go", _]:
            print("Sorry, you can't go that way")

GOING north
GOING east
Sorry, you can't go that way
Sorry, you can't go that way


### Class Pattern

In [61]:
class Click:
    def __init__(self, x, y):
        self.x = x
        self.y = y

class KeyPress:
    def __init__(self, key):
        self.key = key

events = [
    Click(3,4),
    KeyPress("q"),
    Click(5,4)
]

for event in events:
    match event:
        case Click():
            print("GOT A click")
        case _:
            print("NO click")

GOT A click
NO click
GOT A click


In [62]:
for event in events:
    match event:
        case Click() as c:
            print("GOT A click", c.x, c.y)
        case _:
            print("NO click")

GOT A click 3 4
NO click
GOT A click 5 4


In [63]:
for event in events:
    match event:
        case Click(c):
            print("GOT A click", c.x, c.y)
        case _:
            print("NO click")

TypeError: Click() accepts 0 positional sub-patterns (1 given)

In [64]:
class Click:
    def __init__(self, x, y):
        self.x = x
        self.y = y

class KeyPress:
    def __init__(self, key):
        self.key = key

events = [
    Click(3,4),
    KeyPress("q"),
    Click(5,4)
]

for event in events:
    match event:
        case Click(x=x,y=y) if x < y:
            print("GOT an upper-left click")
        case Click():
            print("GOT a click")
        case _:
            print("NO click")

GOT an upper-left click
NO click
GOT a click


In [65]:
for event in events:
    match event:
        case Click(x,y) if x < y:
            print("GOT an upper-left click")
        case Click():
            print("GOT a click")
        case _:
            print("NO click")

TypeError: Click() accepts 0 positional sub-patterns (2 given)

In [66]:
class Click:
    __match_args__ = ('x','y')
    def __init__(self, x, y):
        self.x = x
        self.y = y

class KeyPress:
    def __init__(self, key):
        self.key = key

events = [
    Click(3,4),
    KeyPress("q"),
    Click(5,4)
]

for event in events:
    match event:
        case Click(x,y) if x < y:
            print("GOT an upper-left click")
        case Click():
            print("GOT a click")
        case _:
            print("NO click")

GOT an upper-left click
NO click
GOT a click


In [67]:
from dataclasses import dataclass

@dataclass
class Click:
    x: float
    y: float

class KeyPress:
    def __init__(self, key):
        self.key = key

events = [
    Click(3,4),
    KeyPress("q"),
    Click(5,4)
]

for event in events:
    match event:
        case Click(x,y) if x < y:
            print("GOT an upper-left click")
        case Click():
            print("GOT a click")
        case _:
            print("NO click")

GOT an upper-left click
NO click
GOT a click


### Using defined constants or enumerations

In [73]:
from enum import Enum, auto
from dataclasses import dataclass

class Button(Enum):
    LEFT = auto()
    MIDDLE = auto()
    RIGHT = auto()

@dataclass
class Click:
    x: float
    y: float
    button: Button

class KeyPress:
    def __init__(self, key):
        self.key = key

events = [
    Click(3,4, Button.LEFT),
    KeyPress("q"),
    Click(5,4, Button.RIGHT)
]

for event in events:
    match event:
        case Click(x,y, button=Button.LEFT):
            print("GOT a left click")
        case Click():
            print("GOT a click")
        case _:
            print("NO click")

GOT a left click
NO click
GOT a click


In [74]:
Button.LEFT

<Button.LEFT: 1>

In [77]:
# careful: look what changed
LEFT = Button.LEFT

for event in events:
    match event:
        case Click(x,y, button=Button.LEFT):
            print("GOT a left click")
        case Click():
            print("GOT a click")
        case _:
            print("NO click")
    print(x,y, LEFT)

GOT a left click
3 4 Button.LEFT
NO click
3 4 Button.LEFT
GOT a click
3 4 Button.LEFT


### Mapping Pattern

In [78]:
actions = [
    {'text': "Hello world", "color": "red"},
    {"sleep": 10},
    {"sound": "music://here/song", "format": "mp3"},
    {"sleep": 5, "units": "sec"},
    {"sound": "music://there/song2", "format": "aac", "artist": "A. Singer"}, 
    {"sound": 1234, "format": "mp3", "artist": "A. Singer"},    
]

for action in actions:
    match action:
        case {"text": message, "color": c}:
            print("setting text color", c)
            print(message)
        case {"sleep": duration}:
            print("sleeping", duration)
        case {"sound": str(url), "format": "mp3"}:
            print("playing", url)
        case {"sound": _, "format": format, **rest}:
            print("Unsupported audio format", format, rest)

setting text color red
Hello world
sleeping 10
playing music://here/song
sleeping 5
Unsupported audio format aac {'artist': 'A. Singer'}
Unsupported audio format mp3 {'artist': 'A. Singer'}
